In [1]:
%matplotlib inline
import os
import geopandas as gpd
import matplotlib.pyplot as plt
import pandas as pd
import shapely
import ottawa_libraries as ol
import pulling_library_info

In [2]:
census_file = 'data/dissemination_areas/lda_000b16a_e.shp'
canada_census = gpd.read_file(census_file)

In [3]:
city = "Ottawa - Gatineau (Ontario part / partie de l'Ontario)"
map_data = canada_census[(canada_census.CMANAME==city)].copy()

In [4]:
census_data = pd.read_csv('data/98-401-X2016043_eng_CSV/mini_census.csv')
city_census_data = census_data[census_data['GEO_CODE (POR)'].isin(map_data.CTUID)].copy()
city_pop_data = city_census_data.loc[city_census_data["DIM: Profile of Census Tracts (2247)"]=='Population, 2016'].copy()
city_pop_data['population'] = city_pop_data['Dim: Sex (3): Member ID: [1]: Total - Sex']
city_pop_data = city_pop_data[['GEO_CODE (POR)', 'population']]

In [5]:
city_area_data = city_census_data.loc[city_census_data["DIM: Profile of Census Tracts (2247)"]=='Land area in square kilometres'].copy()
city_area_data['area'] = city_area_data["Dim: Sex (3): Member ID: [1]: Total - Sex"]
city_area_data = city_area_data[['GEO_CODE (POR)', 'area']]

In [6]:
city_density_data = city_census_data.loc[city_census_data["DIM: Profile of Census Tracts (2247)"]=='Population density per square kilometre'].copy()
city_density_data['density'] = city_density_data["Dim: Sex (3): Member ID: [1]: Total - Sex"]
city_density_data = city_density_data[['GEO_CODE (POR)', 'density']]

In [7]:
city_joined = city_area_data.merge(city_pop_data).merge(city_density_data)

In [8]:
# resolves issue with 2 census tracts in Montreal (doesn't impact any of the other top cities)
# TODO: see if '..' codes to something
city_joined['population'] = city_joined['population'].replace('..', 0)
city_joined['density'] = city_joined['density'].replace('..', 0)

In [9]:
city_joined['population'] = pd.to_numeric(city_joined['population'])
city_joined['area'] = pd.to_numeric(city_joined['area'])
city_joined['density'] = pd.to_numeric(city_joined['density'])

In [10]:
map_data['CTUID'] = pd.to_numeric(map_data['CTUID'])

In [11]:
map_data = map_data.merge(right=city_joined, how='left',
                          left_on='CTUID', right_on='GEO_CODE (POR)')

In [12]:
map_data_display = map_data[['geometry', 'population', 'density', 'area']]

Decided to try another colour map. See [here](https://matplotlib.org/stable/tutorials/colors/colormaps.html) for colour map possibilities.

In [14]:
map_data_display.explore(column='density', cmap='cool')